In [5]:
import tensorflow as tf
import tensorflow_hub as hub
import numpy as np

In [6]:
module_url = "https://tfhub.dev/google/universal-sentence-encoder/4" 
model = hub.load(module_url)
print ("module %s loaded" % module_url)

2023-03-07 18:02:24.950608: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:967] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2023-03-07 18:02:24.950776: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-03-07 18:02:24.950861: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublas.so.11'; dlerror: libcublas.so.11: cannot open shared object file: No such file or directory
2023-03-07 18:02:24.950903: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublasLt.so.11'; dlerror: libcublasLt.so.11: cannot open shared object file: No such file or directory
2023-03-07 18:02:24.950943: W tensorf

module https://tfhub.dev/google/universal-sentence-encoder/4 loaded


In [25]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
import numpy as np

#load pandas dataframe (rimuovo le righe vuote che putroppo sono presenti)
vax_series = pd.read_csv('data/posts_ULTRAcleaned_it_only_spacy.csv')
vax_series.dropna(inplace=True)

#salviamo una lista di lista con le parole tokenizzate
vax_text = vax_series['clean_text'].tolist()

vax_text


['pronto affrontare settimana quirinale booster',
 'pass sanitaire guarigione booster pezzo dose migliore dellimmunite covid volere togliere scadenza spg tridosato autorizzare infettare natural arrestatele',
 'vaccinare bambino ricevere almeno dose Italia booster over piano notizia vaccare',
 'sereno sbrocchiamo periodo perch certezza curare grare riconoscente vaccinare booster fatelo vaccino obbligatorio',
 'vaccinare tredoso intero famiglia positivo covid influencer giornalista politico virologo commento proposito Greenpass booster tampono sivax novax emergenza',
 'giovane dovere dose booster unico scudo omicron',
 'booster',
 'continuare ce fregare draghi Milan Juventus inter Venezia quirinale quirinale draghistan vaccino obbligatorio vaccino covid novax dittatura drago vattenere serie tim amico booster greenpassre',
 'esperto israele chiedere somministrazione quarto dose vaccare over proteggere complicazione pi dimezzare rischio contagio covid israel booster',
 'inter inzago positi

In [26]:
import spacy
import pandas as pd
import regex as re
import nltk
from nltk.stem.snowball import SnowballStemmer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
it_stopwords = stopwords.words('italian')

#the stemmer requires a language parameter
snow_stemmer = SnowballStemmer(language='italian')

def cleaner(s):
    #removing numbers and special caracters
    s = re.sub(r'[^a-z\s]', '', s).strip()
    #remving multiple spaces
    s = " ".join(s.split()).strip()
    #some manual corrections
    #s = s.replace(' accino', ' vaccino')
    #removing stopwords with nltk
    s = stop_word_remover(s)
    #stemming with nltk
    s = stemmer(s)

    return s


def stop_word_remover(text):
    word_tokens = word_tokenize(text)
    word_list = [word for word in word_tokens if word.lower() not in it_stopwords]
    return " ".join(word_list)

def stemmer(text):
    words = word_tokenize(text)
    stem_words = [snow_stemmer.stem(word) for word in words]
    return " ".join(stem_words)

query = "Secondo tutte le leggi conosciute dell’aeronautica, non c’è modo che un ape sia in grado di volare. Le sue ali sono troppo piccole per sollevare il suo corpicino grassoccio da terra. L’ape, si sa, vola lo stesso. Perché alle api non interessa quello che gli uomini ritengono impossibile"
query=cleaner(query)

print(query)


econd tutt legg conosc dellaeronaut mod ape grad vol ali tropp piccol sollev corpicin grassocc terr ape sa vol stess erch api interess uomin riteng imposs


In [31]:
sentence_embeddings = model(vax_text)

query_vec = model([query])[0]

In [32]:
from scipy.spatial.distance import cosine, euclidean

for sent in vax_text:
  sim = 1 - cosine(query_vec, model([sent])[0])
  #sim = cosine(query_vec, sent)
  print("Sentence = ", sent, "; similarity = ", sim)

Sentence =  pronto affrontare settimana quirinale booster ; similarity =  0.180622398853302
Sentence =  pass sanitaire guarigione booster pezzo dose migliore dellimmunite covid volere togliere scadenza spg tridosato autorizzare infettare natural arrestatele ; similarity =  0.42423611879348755
Sentence =  vaccinare bambino ricevere almeno dose Italia booster over piano notizia vaccare ; similarity =  0.23023852705955505
Sentence =  sereno sbrocchiamo periodo perch certezza curare grare riconoscente vaccinare booster fatelo vaccino obbligatorio ; similarity =  0.39001432061195374
Sentence =  vaccinare tredoso intero famiglia positivo covid influencer giornalista politico virologo commento proposito Greenpass booster tampono sivax novax emergenza ; similarity =  0.39018571376800537
Sentence =  giovane dovere dose booster unico scudo omicron ; similarity =  0.23945236206054688
Sentence =  booster ; similarity =  0.06363954395055771
Sentence =  continuare ce fregare draghi Milan Juventus in